## Inlezen LKM25 links
Lees in kolom nodefrom en nodeto: lkm25\Schematisatie\KRWVerkenner\shapes\LKM25_Links.shp

- vinden LSW eindpunten
- Per eindpunt LKM-links naar lopen tot node_to start met LSM
- Zoek SOBEK
- Wanneer LSW ID gelijk is aan nodefrom: volg het netwerk totdat nodeto start met LSM. 
- Check nu of er een Sobek lateral op minder dan 250m. ligt. Zoja verbindt deze LSM met deze SOBEK lateral. 
Zoniet loop het netwerk verder af en check nogmaals of het volgende eindpunt wel op 250m. van een lateral ligt.
Let op: Je mag alleen Sobek laterals gebruiken die in hetzelfde district liggen als de LSW. 

In [39]:
from config import DATA_DIR, LKM25_DIR, MOZART_DIR, LSW_DIR, LSM_KOPPELING_DIR, load_src
import geopandas as gpd
load_src()

from lhm.read import read_lsm_lhm, read_lsw_routing
from lhm.lsm import snap_to_waterbodies
from lhm.lsw import lsw_end_nodes, lsw_network

## Inlezen LSWs

Vanuit de geleverde `lsws.shp` en `lswrouting.dik` maken we een netwerk van LSWs.

In [40]:
lsw_routing_dik = MOZART_DIR / r"mozartin/lswrouting.dik"
lsw_routing_df = read_lsw_routing(lsw_routing_dik)
lsw_gdf = gpd.read_file(LSW_DIR / "lsws.shp")

lsw_gdf = lsw_gdf.dissolve(by="LSWFINAL").reset_index()
lsw_links_gdf, lsw_nodes_gdf = lsw_network(lsw_gdf, lsw_routing_df)

## Vinden niet-gekoppelde LSWs

We gaan ervan uit dat LSWs die afwateren op andere LSWs níet tevens afwateren op het DM. We gaan vanaf dit punt LSWs die niet gekoppeld zijn aan andere LSWs koppelen aan het DM. Hieronder tonen we deze LSWs op de kaart

In [41]:
lsw_end_nodes_gdf = lsw_end_nodes(lsw_links_gdf, lsw_gdf)
print(f"we moeten {len(lsw_end_nodes_gdf)} koppelen aan DM-knopen")
lsw_end_nodes_gdf.explore()

we moeten 2309 koppelen aan DM-knopen


## Koppelen via DW-keys

Vanuit `dwkeys.txt`kunnen we per district kijken aan welke DM knoop wordt gekoppeld. Wanneer een district slechts koppelt aan 1 DM-knoop, dan betekent dit dat alle LSWs in dit district gekoppeld moeten worden aan deze knoop.

We doen dit en tonen de overgebleven nog niet gekoppelde LSWs.

In [42]:
from lhm.read import read_dw_keys
from config import LHM_DIR

dw_key_file = LHM_DIR / r"dm/txtfiles_git/dwkeys.txt"

dw_keys_df = read_dw_keys(dw_key_file)
lsw_dm_links = []

for dw, df in dw_keys_df.groupby(by=["oid"]):
    dm_nodes = df.loc[df.kty == "d"].nid.unique()
    if len(dm_nodes) == 1:
        df = lsw_end_nodes_gdf[lsw_end_nodes_gdf["DWRN"] == dw[0]]
        for row in df.itertuples():
            lsw_dm_links += [(row.LSWFINAL, dm_nodes[0])]

print(f"{len(lsw_dm_links)} LSWs gekoppeld aan DM-knopen")
lsw_end_nodes_gdf = lsw_end_nodes_gdf.loc[~lsw_end_nodes_gdf.LSWFINAL.isin([i[0] for i in lsw_dm_links])]
print(f"We moeten nog {len(lsw_end_nodes_gdf)} koppelen aan DM-knopen")
lsw_end_nodes_gdf.explore()

1783 LSWs gekoppeld aan DM-knopen
We moeten nog 526 koppelen aan DM-knopen


## Koppelen via de LSM-LHM koppeling

### Koppelen LSM lateralen aan het DM
Vanuit de bestanden `LSM3_locations.csv`, `LSM3_DMKnoopDistrict_childs.csv` kunnen we uitzoeken hoe aan welke DM-knoop een LSM-lateraal is gekoppeld. Een LSM-lateraal ligt meestal vrij netjes in het watersysteem geschematiseerd.

In [43]:
lsm3_locations_csv = LSM_KOPPELING_DIR / "LSM3_locations.csv"
knoop_district_csv = LSM_KOPPELING_DIR / "LSM3_DMKnoopDistrict_childs.csv"
lsm_lhm_gdf = read_lsm_lhm(lsm3_locations_csv, knoop_district_csv)

lsm_lhm_gdf.explore()

### Koppelen LSW via LSM-lateralen aan DM
Voor de nog overgebleven LSWs zoeken we de DM-knoop via LSM-lateralen. We nemen deze stappen:
1. We kijken of er LSM-lateralen van het juist district liggen in het gebied van de LSW
2. We kijken aan welke unieke DM-knopen deze lateralen zijn verbonden. We verbinden de LSW met al deze districten

In [44]:
lkm_waterlichamen_shp = LKM25_DIR / "KRW-waterlichamen_SGBP3.shp"
lkm_waterlichamen_gdf = gpd.read_file(lkm_waterlichamen_shp)
lsm_lhm_snapped_gdf = snap_to_waterbodies(lsm_lhm_gdf, lkm_waterlichamen_gdf, offset=100)

lkm_links_shp = LKM25_DIR / "LKM25_Links.shp"
lkm_links_gdf = gpd.read_file(lkm_links_shp)

In [45]:
dw_keys_df[dw_keys_df.oid == 30]

oid kty  rid   nid                                    ds cp node_to   
208   30   e    0  6057        Inlaatduiker bij gemaal Colijn  v    None  \
209   30   e    0  6058      Blocq van Kuffeler (Zuidersluis)  v    None   
210   30   d    0  6057                         Gemaal Colijn  v    6057   
211   30   d    0  6058  Gemalen Wortman & Blocq van Kuffeler  v    6058   
212   30   d    0  6059                         Gemaal Lovink  v    6059   

    node_from  
208      6057  
209      6058  
210      None  
211      None  
212      None

In [46]:
from shapely.geometry import Point
from lhm.dm import get_dm_nodes

if lsw_gdf.index.name !="LSWFINAL":
    lsw_gdf.set_index("LSWFINAL", inplace=True)
init = len(lsw_dm_links)

def find_links(row, lsw_id): # algemene functie om links te vinden mbv een LKM link
    lsw_dm_links = [] 
    polygon = lsw_gdf.at[lsw_id, "geometry"]
    df = lsm_lhm_gdf[lsm_lhm_gdf.within(polygon)]# we kijken of er lateralen in het gebied van de LSW liggen
    if not df.empty:
        lsw_dm_links +=[(lsw_id, i) for i in df.DM.unique()]
    if row.nodeto.startswith("LSM"): # de link moet starten met LSM
        point = Point(row.geometry.bounds[2:]) # de Point van de nodeto
        waterlichaam_gdf = lkm_waterlichamen_gdf[lkm_waterlichamen_gdf.intersects(point)] # het waterlichaam waar punt op snapt
        if not waterlichaam_gdf.empty: # er moet wél een waterlichaam gevonden worden
            waterlichaam = waterlichaam_gdf.iloc[0] # dan pakken we het eerste waterlichaam (als het goed is is de lengte altijd 1)
            df = lsm_lhm_snapped_gdf[lsm_lhm_snapped_gdf.within(waterlichaam.geometry)] # we zoeken naar lsm_lhm laterale knopen binnen het waterlichaam
            if not df.empty: # we hebben gevonden!
                lsw_dm_links = [(lsw_id, i) for i in df.DM.unique()] # hier maken we links van de lsw_id naar de unieke DM-knopen   
                lsw_dm_links = [i for i in lsw_dm_links if i[1] in dm_nodes_stringified]
    return lsw_dm_links


all_links = []
for row in lsw_end_nodes_gdf.itertuples():
    lsw_id = row.LSWFINAL
    print(lsw_id)
    district = row.DWRN
    dm_nodes = get_dm_nodes(dw_keys_df,district)
    dm_nodes_stringified = [str(element) for element in dm_nodes]
    lkm_links_iter = lkm_links_gdf[lkm_links_gdf.nodefrom == str(lsw_id)].itertuples() 
    for row in lkm_links_iter:
        links = []
        links = find_links(row, lsw_id) 
        if (not links):
            counter = 0
            while (not links) and (counter < 50) :
                df = lkm_links_gdf[lkm_links_gdf.nodefrom == row.nodeto]
                if not df.empty:
                    row = df.iloc[0]
                    links = find_links(row, lsw_id)
                counter += 1
        all_links += [i for i in links if i not in all_links]

all_links       
print(f"{len(all_links)} LSWs koppelingen gemaakt aan DM-knopen") 
lsw_end_nodes_gdf = lsw_end_nodes_gdf.loc[~lsw_end_nodes_gdf.LSWFINAL.isin([i[0] for i in all_links])]
print(f"We moeten {len(lsw_end_nodes_gdf)} koppelen aan DM-knopen")
lsw_end_nodes_gdf.explore()

11114
11120
11184
11208
11214
11216
11248
11256
11304
11313
11314
11316
11339
11342
11353
11377
11395
11396
11397
11399
11421
11423
20011
20015
20016
20017
20018
20020
20021
20023
20032
20034
20036
20037
20042
20043
20052
20053
20054
20055
20056
20057
20058
20060
20062
20063
20065
20071
20072
20077
20078
20079
20081
20084
20088
20092
20093
20098
20100
20102
20103
20105
20106
20107
21012
21016
21017
30001
30004
30008
30011
30015
30018
30085
30097
30114
30141
30144
30152
30153
30154
30155
30158
30159
31077
31101
31230
70001
70002
70011
70017
70021
70022
70025
70026
70029
70082
70083
70085
70089
70090
70114
70116
70119
70121
70124
70125
71023
71030
71067
80109
80110
80111
80136
80238
80243
80347
90001
90002
90003
90011
90027
90029
90031
90032
90033
90037
90038
90043
90044
90071
90072
90074
90075
90076
90077
90078
90083
90087
90096
90097
90103
90112
90115
90116
90117
90124
90126
90127
90139
90149
90160
100096
100103
100104
100123
100147
100148
100152
100173
100175
100180
100182
100189
1002

Koppelen via het LKM (in ontwikkeling)